In [ ]:
# ..... annotate CM cells ..... #

In [2]:
library(Seurat)
library(SingleCellExperiment)
library(MetaMarkers)
library(data.table)
library(dplyr)

In [3]:
# load list of orthologs
om = read.delim('mouse_chicken_orthologs_biomart.txt', sep = '\t')
colnames(om) <- c('mouse', 'chicken', 'LCA', 'homology_type')
om <- om[om[,1]!='' & om[,2]!='' & om$homology_type=='ortholog_one2one',]
dim(om)
om[1,]

[1] 12287     4

mouse  chicken LCA     homology_type   
6 mt-Nd1 ND1     Amniota ortholog_one2one

In [26]:
# load markers
markers = fread('~/septation/devCellPy_markers_res3.csv.gz')
markers$gene <- om$chicken[match(markers$gene, om$mouse)]
markers <- markers[!is.na(markers$gene),]
ctypes = unique(markers$cell_type)

# get top n markers for each cell type
markers$rank = NA
for(ii in 1:length(ctypes)){
    id = which(markers$cell_type==ctypes[ii])
    markers$rank[id] = 1:length(id)
}
markers[1:2,]

# tibble of group, cell_type, gene, rank
top_markers = as_tibble(markers[which(markers$rank<=200),c('group', 'cell_type', 'gene', 'rank', 'fold_change', 'auroc')])
top_markers[1:2,]

group cell_type gene  fold_change auroc     log_fdr    population_size
1 all   LV CM     HAND1 4.105356    0.8644412 -1096.8747 1535           
2 all   LV CM     MYL2  2.791375    0.8127003  -807.3052 1535           
  population_fraction average_expression se_expression detection_rate
1 0.100821             193.3223            3.822618    0.9022801     
2 0.100821            7284.1360          115.571293    0.9687296     
  fold_change_detection precision recall    rank
1 4.074849              0.3143441 0.9022801 1   
2 2.075061              0.1889214 0.9687296 2

group cell_type gene  rank fold_change auroc    
1 all   LV CM     HAND1 1    4.105356    0.8644412
2 all   LV CM     MYL2  2    2.791375    0.8127003

In [5]:
# get list of samples
stages = c(rep('stage23', 2), rep(c('stage28', 'stage32'), each = 3))
samples = c('sample3', 'sample10', 'sample5', 'sample10', 'sample11',
           'sample5', 'sample10', 'sample12')

In [47]:
# load data
id1 = 8
currstage1 = stages[id1]
currsmp1 = samples[id1]
sc1 = readRDS(paste0(currstage1, '_', currsmp1, '_data.rds'))

# load previous marker set (KS)
newdf2 = read.delim(paste0(currstage1, '_', currsmp1, '_Knight-Schrijver_celltypes.csv'), sep = ',')
sc1$class = newdf2$class[match(colnames(sc1), newdf2$barcode)]
sc1 <- sc1[,sc1$class %in% 'Cardiomyocytes']

# get SCE object
sc3 = SingleCellExperiment(list(counts = GetAssayData(sc1, 'counts')))
colData(sc3) <- DataFrame(sc1@meta.data)
assay(sc3, "cpm") = convert_to_cpm(assay(sc3))

In [48]:
# predict cell type neighborhood
ct_scores = score_cells(log1p(cpm(sc3)), top_markers)
ct_enrichment = compute_marker_enrichment(ct_scores)
ct_pred = assign_cells(ct_scores)

ct_pred[1:3,]
table(ct_pred$predicted)

group predicted score    enrichment
stage32_sample12_AAACCCAAGTCATACC-1 all   Septal CM 2.476111 1.047703  
stage32_sample12_AAACGAACACGCACCA-1 all   LV CM     1.271880 1.060092  
stage32_sample12_AAAGAACCAAGACAAT-1 all   LV CM     1.897793 1.018477


    LV CM     RV CM Septal CM 
      567       124      1043 

In [49]:
# save
newdf = data.frame(barcode = rownames(ct_pred), celltype = ct_pred$predicted)
newdf[1,]
write.table(newdf, file = paste0(currstage1, '_', currsmp1, '_CM_subtypes.csv'),
            sep = ',', row.names = F, col.names = T, quote = F)

barcode                             celltype 
1 stage32_sample12_AAACCCAAGTCATACC-1 Septal CM